# Analysis of AWS S3 Access Log Data

In [1]:
import numpy as np
import pandas as pd
from bokeh.charts import (output_notebook, output_file, show, 
                          Scatter, Histogram, TimeSeries, BoxPlot)
from bokeh.plotting import figure, ColumnDataSource
from bokeh.models import Range1d, HoverTool, ResizeTool
from bokeh.layouts import column, row, gridplot
output_notebook()

Loading BokehJS ...

Read the log data and replace column values of `-` with `None`:

In [2]:
s3l = pd.read_csv('../../../s3log-cloudydap-201703.csv')
s3l.replace(['-'], [None]);

/Users/ajelenak/Documents/dmr++/lib/python3.5/site-packages/IPython/core/interactiveshell.py:2717: DtypeWarning: Columns (13,15) have mixed types. Specify dtype option on import or set low_memory=False.
  interactivity=interactivity, compiler=compiler, result=result)


What was just read from the CSV file?

In [3]:
s3l.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 2184269 entries, 0 to 2184268
Data columns (total 19 columns):
Bucket_Owner           object
Bucket                 object
Time                   object
Remote_IP              object
Requester              object
Request_ID             object
Operation              object
Key                    object
HTTP_method            object
Request_URI            object
HTTP_status            int64
Error_Code             object
Bytes_Sent             int64
Object_Size            object
Total_Time_ms          int64
Turn_Around_Time_ms    object
Referrer               object
User_Agent             object
Version_Id             object
dtypes: int64(3), object(16)
memory usage: 316.6+ MB


## Data Preprocessing

Remove not needed columns:

In [4]:
s3l.drop(['Bucket', 'Bucket_Owner', 'Referrer', 'Version_Id'], axis=1, inplace=True)

Extract information from the `cloudydap` URL parameter into new columns. The format of the values is either of the two:

    {Use case}_{Architecture}_STARTED_{Use case run ID}
    {Use case}_{Architecture}_{Use case run ID}
    
**NOTE**: The `{Use case}` field may contain underscores!

In [5]:
cloudydap_info = s3l.Request_URI.str.extract(
    '[?&]cloudydap=(?P<use_case>.+)_(?P<arch>A[^_]+)_(?:STARTED_)?(?P<uc_run_id>.+)\.h5&?', 
    expand=True)
s3l = pd.concat([s3l, cloudydap_info], axis=1);

Make sure the cloudydap information is successfully parsed for each entry:

In [6]:
if s3l[['arch', 'use_case', 'uc_run_id']].isnull().any().any():
    raise ValueError('Parsing cloudydap parameter values failed')

Remove the Request_URI column now:

In [7]:
s3l.drop(['Request_URI'], axis=1, inplace=True)

Convert the Time column to datetime objects:

In [8]:
s3l['Time'] = pd.to_datetime(s3l['Time'])

What we have now?

In [9]:
s3l.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 2184269 entries, 0 to 2184268
Data columns (total 17 columns):
Time                   datetime64[ns]
Remote_IP              object
Requester              object
Request_ID             object
Operation              object
Key                    object
HTTP_method            object
HTTP_status            int64
Error_Code             object
Bytes_Sent             int64
Object_Size            object
Total_Time_ms          int64
Turn_Around_Time_ms    object
User_Agent             object
use_case               object
arch                   object
uc_run_id              object
dtypes: datetime64[ns](1), int64(3), object(13)
memory usage: 283.3+ MB


Sort rows based on column Time:

In [10]:
s3l.sort_values(by='Time', ascending=True);

Activate the cell below if selecting data by time:

s3l = s3l[(s3l.Time >= '2017-02-28') & (s3l.Time <= '2017-03-01T06:00:00')]

In [11]:
s3l = s3l[(s3l.Time >= '2017-03-12T06:08:00') & (s3l.Time <= '2017-03-14T13:32:00')]

Time span of the S3 access data:

In [12]:
print('Start: {}\nEnd:   {}'.format(s3l.Time.min(), s3l.Time.max()))

Start: 2017-03-12 06:08:17
End:   2017-03-14 13:31:59


# Data Cleanup

Search for any log entry that indicates some sort of error.

What are the S3 operations:

In [13]:
s3l.Operation.unique()

array(['REST.GET.OBJECT'], dtype=object)

What are the different HTTP status codes:

In [14]:
s3l['HTTP_status'].unique()

array([206, 200, 404, 500, 416])

What are the different AWS S3 system error codes:

In [15]:
s3l.Error_Code.unique()

array(['-', 'NoSuchKey', 'InternalError', 'InvalidRange'], dtype=object)

Find the _bad_ S3 requests:

In [16]:
bad_reqs = (s3l['HTTP_status'] >= 400) | (s3l['Error_Code'] != '-')

In [17]:
s3l.loc[bad_reqs, ['HTTP_status', 'Error_Code', 'Key', 'HTTP_method', 'User Agent']]

HTTP_status     Error_Code  \
800853           404      NoSuchKey   
801834           404      NoSuchKey   
961780           404      NoSuchKey   
962777           404      NoSuchKey   
987645           404      NoSuchKey   
991570           404      NoSuchKey   
1010302          404      NoSuchKey   
1017926          404      NoSuchKey   
1021011          404      NoSuchKey   
1023873          404      NoSuchKey   
1025820          500  InternalError   
1029474          404      NoSuchKey   
1029929          404      NoSuchKey   
1032406          404      NoSuchKey   
1033514          404      NoSuchKey   
1033776          404      NoSuchKey   
1033777          404      NoSuchKey   
1036083          404      NoSuchKey   
1039474          404      NoSuchKey   
1040138          404      NoSuchKey   
1045384          404      NoSuchKey   
1252080          404      NoSuchKey   
1546117          500  InternalError   
1648773          500  InternalError   
1738549          404      NoSuchKey   
1742349          404      NoSuchKey   
1764450          404      NoSuchKey   
1773033          416   InvalidRange   
2017890          404      NoSuchKey   
2042331          404      NoSuchKey   

                                                 Key HTTP_method  User Agent  
800853   bytestream/6389aba2ced43ef4796ee89d8d8414d9         GET         NaN  
801834   bytestream/094e70793148a97742191430ccea74c7         GET         NaN  
961780   bytestream/0f66edc0d3b8d3c77bc5481b5088a5fc         GET         NaN  
962777   bytestream/671e319145cf87e8777ef83ca082bfb3         GET         NaN  
987645   bytestream/094e70793148a97742191430ccea74c7         GET         NaN  
991570   bytestream/094e70793148a97742191430ccea74c7         GET         NaN  
1010302  bytestream/671e319145cf87e8777ef83ca082bfb3         GET         NaN  
1017926  bytestream/adb99ec2a68b1d16fc9cd2f1d33e983d         GET         NaN  
1021011  bytestream/adb99ec2a68b1d16fc9cd2f1d33e983d         GET         NaN  
1023873  bytestream/adb99ec2a68b1d16fc9cd2f1d33e983d         GET         NaN  
1025820  bytestream/20396619880bc6a6c1e3b1309459940e         GET         NaN  
1029474  bytestream/adb99ec2a68b1d16fc9cd2f1d33e983d         GET         NaN  
1029929  bytestream/adb99ec2a68b1d16fc9cd2f1d33e983d         GET         NaN  
1032406  bytestream/adb99ec2a68b1d16fc9cd2f1d33e983d         GET         NaN  
1033514  bytestream/adb99ec2a68b1d16fc9cd2f1d33e983d         GET         NaN  
1033776  bytestream/adb99ec2a68b1d16fc9cd2f1d33e983d         GET         NaN  
1033777  bytestream/adb99ec2a68b1d16fc9cd2f1d33e983d         GET         NaN  
1036083  bytestream/adb99ec2a68b1d16fc9cd2f1d33e983d         GET         NaN  
1039474  bytestream/adb99ec2a68b1d16fc9cd2f1d33e983d         GET         NaN  
1040138  bytestream/adb99ec2a68b1d16fc9cd2f1d33e983d         GET         NaN  
1045384  bytestream/adb99ec2a68b1d16fc9cd2f1d33e983d         GET         NaN  
1252080  bytestream/09fcc13d3032fe4cf88398bc2b248e25         GET         NaN  
1546117  bytestream/d600c270d80603dba3732b531342d4d5         GET         NaN  
1648773  bytestream/e101c7713ec07f243492023adde2a0f2         GET         NaN  
1738549  bytestream/e47858f9e5008a88694ca10f6a3eb0ec         GET         NaN  
1742349  bytestream/ec2b3d664cfbfd9217e74738bbcd281f         GET         NaN  
1764450  bytestream/ec2b3d664cfbfd9217e74738bbcd281f         GET         NaN  
1773033  bytestream/a9b7606968676513a03ccc50de868f08         GET         NaN  
2017890  bytestream/7433615f0ae004633d54fc76e4a7f6f0         GET         NaN  
2042331  bytestream/c6af25fa0ef58d8d6383cce9dcc12f00         GET         NaN

Break down bad S3 requests per day and hour:

In [18]:
s3l.loc[bad_reqs, 'Time']\
    .apply(lambda t: pd.Series({'date': t.date(), 'hour': t.hour}))\
    .groupby(['date', 'hour'])\
    .size()

date        hour
2017-03-12  12       2
2017-03-13  6        2
            7        3
            8       14
            16       1
            21       1
2017-03-14  0        1
            2        4
            11       1
            12       1
dtype: int64

How many bad requests per architecture and use case:

In [19]:
s3l.loc[bad_reqs].groupby(['arch', 'use_case']).size()

arch   use_case
A2CFT  UC20         1
A3CFT  UC18        19
       UC2          2
       UC20         6
       UC21         2
dtype: int64

Remove bad S3 log entries:

In [20]:
s3l.drop(s3l[bad_reqs].index, inplace=True)

Number of rows now:

In [21]:
len(s3l.index)

1310427

## Helper Functions

### Transfer Rate

Calculate transfer rate for each S3 request as a new column. The formula is:
    
$$0.001 * \frac{Bytes\_Sent}{Total\_Time\_ms - Turn\_Around\_Time\_ms}\,\,\rm{MBytes/s}$$

Transfer rate for cases where total and turnaround time are equal (very fast data transfer) will be equal to the largest transfer rate calculated. This avoids having to deal with `inf` values.

In [22]:
def s3_transf_rate(df):
    tr = 0.001 * df['Bytes_Sent'] / (df['Total_Time_ms'] - df['Turn_Around_Time_ms'])
    infs = np.isinf(tr)
    tr[infs] = tr[~infs].max()
    return tr

### Bytes Savings

Reduction in the number of bytes pulled out of S3 compared to the original object size.

In [23]:
def s3_bytes_savings(df):
    """Calculate the total percentage reduction in the bytes returned from S3 compared
       to the original object sizes.
       
       df: Input pandas DataFrame.
    """
    return (df['Bytes_Sent'].sum()/df['Object_Size'].sum() - 1) * 100

### Grid of Boxplots

Produce a grid of boxplots for a specific column of the DataFrame and a list of use cases. Breakdown the column data per architecture.

In [24]:
def uc_boxplots(df, col, uc_list=None, width=300, height=300):
    if uc_list is None:
        uc_list = df.use_case.unique()

    g = list()
    for uc in sorted(uc_list):
        p = BoxPlot(df[df.use_case == uc], values=col, 
                    title='Use Case: {}'.format(uc),
                    label=['arch'], 
                    outliers=False,
                    color='arch',
                    legend='top_right')
        g.append(p)

    show(gridplot(g, ncols=2, plot_width=width, plot_height=height, 
                  toolbar_location='left'))

## General Data Exploration

Convert the Turn_Around_Time_ms and Object_Size columns to numbers (I don't know why it is not in the first place):

In [25]:
s3l['Turn_Around_Time_ms'] = pd.to_numeric(s3l['Turn_Around_Time_ms'])
s3l.Object_Size = pd.to_numeric(s3l.Object_Size)

Calculate the transfer rate in MBytes/sec for every S3 request:

In [26]:
s3l['Trans_Rate_MB/s'] = s3_transf_rate(s3l)

User agent list:

In [27]:
s3l.User_Agent.unique()

array(['-',
       'libcurl/7.19.7 NSS/3.21 Basic ECC zlib/1.2.3 libidn/1.18 libssh2/1.4.2'], dtype=object)

How many different architectures:

In [28]:
s3l.arch.unique()

array(['A2CFT', 'A3CFT', 'A1CFT'], dtype=object)

How many different use cases:

In [29]:
s3l.use_case.unique()

array(['UC6', 'UC7', 'UC2', 'UC10', 'UC11', 'UC12', 'UC13', 'UC14', 'UC15',
       'UC16', 'UC17', 'UC18', 'UC19', 'UC20', 'UC21'], dtype=object)

How many different use case run IDs:

In [30]:
s3l.uc_run_id.unique()

array(['1489300078', '1489300299', '1489298903', '1489300485',
       '1489298899', '1489298896', '1489304047', '1489304190',
       '1489304325', '1489307764', '1489307950', '1489308126',
       '1489311677', '1489312051', '1489312485', '1489313617',
       '1489313915', '1489314168', '1489315283', '1489315808',
       '1489316475', '1489317580', '1489318683', '1489319771',
       '1489320897', '1489323159', '1489322045', '1489325431',
       '1489326608', '1489324290', '1489327766', '1489327998',
       '1489328590', '1489329530', '1489329755', '1489330091',
       '1489330272', '1489330458', '1489330708', '1489328391',
       '1489328845', '1489329350', '1489329938', '1489328995',
       '1489329174', '1489328221', '1489330896', '1489331116',
       '1489331386', '1489331540', '1489331806', '1489335411',
       '1489339014', '1489342594', '1489345993', '1489349387',
       '1489352793', '1489356223', '1489359681', '1489363090',
       '1489366701', '1489367147', '1489367367', '14893

Count of S3 requests for each architecture:

In [31]:
s3l.arch.value_counts().sort_index()

A1CFT     10446
A2CFT    659432
A3CFT    640549
Name: arch, dtype: int64

Count of S3 requests for each use case:

In [32]:
s3l.use_case.value_counts()

UC20    573302
UC21    290951
UC18    193429
UC19    173482
UC15     23353
UC14     22957
UC13     14096
UC11      6204
UC12      3873
UC6       2169
UC17      2144
UC10      1825
UC16      1470
UC7       1097
UC2         75
Name: use_case, dtype: int64

Number of S3 requests per use case and architecture:

In [33]:
s3l.groupby(['use_case', 'arch']).size().unstack()

arch       A1CFT     A2CFT     A3CFT
use_case                            
UC10       365.0     730.0     730.0
UC11       364.0    2920.0    2920.0
UC12       439.0    1717.0    1717.0
UC13       438.0    6829.0    6829.0
UC14      4387.0    9499.0    9071.0
UC15      3649.0   10218.0    9486.0
UC16         NaN     722.0     748.0
UC17         NaN    1066.0    1078.0
UC18         NaN   96839.0   96590.0
UC19         NaN   86753.0   86729.0
UC2          NaN       4.0      71.0
UC20         NaN  292221.0  281081.0
UC21         NaN  148682.0  142269.0
UC6        439.0     865.0     865.0
UC7        365.0     367.0     365.0

Change in the number of S3 requests between different architectures:

In [34]:
x = s3l.groupby(['arch', 'use_case']).size()

In [35]:
x['A2CFT'] - x['A1CFT']

use_case
UC10     365.0
UC11    2556.0
UC12    1278.0
UC13    6391.0
UC14    5112.0
UC15    6569.0
UC16       NaN
UC17       NaN
UC18       NaN
UC19       NaN
UC2        NaN
UC20       NaN
UC21       NaN
UC6      426.0
UC7        2.0
dtype: float64

In [36]:
x['A3CFT'] - x['A1CFT']

use_case
UC10     365.0
UC11    2556.0
UC12    1278.0
UC13    6391.0
UC14    4684.0
UC15    5837.0
UC16       NaN
UC17       NaN
UC18       NaN
UC19       NaN
UC2        NaN
UC20       NaN
UC21       NaN
UC6      426.0
UC7        0.0
dtype: float64

In [37]:
x['A3CFT'] - x['A2CFT']

use_case
UC10        0
UC11        0
UC12        0
UC13        0
UC14     -428
UC15     -732
UC16       26
UC17       12
UC18     -249
UC19      -24
UC2        67
UC20   -11140
UC21    -6413
UC6         0
UC7        -2
dtype: int64

Timeline of all S3 requests:

p = figure(x_axis_type='datetime', toolbar_location='above')
p.xaxis.axis_label = 'Time of S3 request'
p.yaxis.axis_label = 'Total S3 request time [ms]'
p.segment(x0=s3l['Time'], y0=([0] * len(s3l['Total_Time_ms'])), 
          x1=s3l['Time'], y1=s3l['Total_Time_ms'], 
          line_alpha=0.5)
p.circle(s3l['Time'], s3l['Total_Time_ms'])
p.add_tools(ResizeTool())
show(p)

## Select Performance Comparison between Architectures

In [38]:
grp = s3l.groupby('arch')

### S3 Total Time

In [39]:
grp['Total_Time_ms'].describe().unstack()

count         mean          std     min     25%     50%     75%  \
arch                                                                        
A1CFT   10446.0  3330.939498  2410.781596  1455.0  1599.0  2185.5  4520.0   
A2CFT  659432.0    41.476932   147.034715     5.0    10.0    16.0    27.0   
A3CFT  640549.0    72.259204   186.366450     3.0    30.0    44.0    71.0   

           max  
arch            
A1CFT  68037.0  
A2CFT  58931.0  
A3CFT  60758.0

In [40]:
p = BoxPlot(s3l, values='Total_Time_ms', label=['arch'],
           color='arch',
           outliers=False,
           legend='top_right')
show(p)

### S3 Turnaround Time

In [41]:
grp['Turn_Around_Time_ms'].describe().unstack()

count        mean        std   min   25%   50%    75%      max
arch                                                                    
A1CFT   10446.0  118.012253  96.993696  42.0  83.0  99.0  126.0   6100.0
A2CFT  659432.0   27.527339  65.442305   5.0   9.0  13.0   24.0  15858.0
A3CFT  640549.0   57.349597  75.520149   2.0  29.0  42.0   65.0  17203.0

In [42]:
p = BoxPlot(s3l, values='Turn_Around_Time_ms', label=['arch'],
           color='arch',
           outliers=False,
           legend='top_right')
show(p)

### Transfer Rates

In [43]:
grp['Trans_Rate_MB/s'].describe().unstack()

count        mean         std       min        25%        50%  \
arch                                                                      
A1CFT   10446.0   70.066337   11.166009  4.675489  70.040226  73.076566   
A2CFT  659432.0  107.507218  163.363410  0.000008  37.075000  41.765000   
A3CFT  640549.0  149.340187  194.366834  0.000005  38.070000  43.038000   

             75%         max  
arch                          
A1CFT   76.24934   81.798303  
A2CFT   80.61900  544.513000  
A3CFT  121.92150  544.513000

In [44]:
p = BoxPlot(s3l, values='Trans_Rate_MB/s', label=['arch'],
           color='arch',
           outliers=False,
           legend='top_left')
show(p)

### Bytes Sent

These are bytes transferred from S3 to Hyrax server.

In [45]:
grp['Bytes_Sent'].describe().unstack()

count          mean           std          min          25%  \
arch                                                                    
A1CFT   10446.0  2.066004e+08  1.013718e+08  112519317.0  112888124.0   
A2CFT  659432.0  9.784629e+04  1.307926e+05          4.0      37764.0   
A3CFT  640549.0  9.746074e+04  1.294957e+05          8.0      37735.0   

               50%          75%          max  
arch                                          
A1CFT  113083656.0  318357415.0  323612711.0  
A2CFT      41177.0     175468.0    1112792.0  
A3CFT      41139.0     175287.0    1112792.0

## Architecture 1

S3 requests for Architecture 1:

In [46]:
a1 = s3l[s3l.arch == 'A1CFT']
len(a1.index)

10446

For Architecture \#1, the number of bytes sent and object size should be the same for all S3 requests:

In [47]:
(a1.Bytes_Sent == a1.Object_Size).all()

True

Percentage reduction in the number of bytes pulled out of S3 compared to the original object sizes:

In [48]:
s3_bytes_savings(a1)

0.0

In [49]:
p = Histogram(a1['Total_Time_ms'], bins=100, title='Architecture 1 (All Use Cases)',
              xlabel='Total S3 response time [ms]', ylabel='Count(S3 requests)')
p.x_range = Range1d(0, 25000)
show(p)

In [50]:
p = BoxPlot(a1, values='Total_Time_ms', label=['use_case'], 
            title='Architecture 1 (group by Use Case)',
            outliers=False,
            legend=False)
show(p)

In [51]:
p = Histogram(a1['Turn_Around_Time_ms'], bins=50, title='Architecture 1 (All Use Cases)',
              xlabel='Turn-around S3 time [ms]', ylabel='Count(S3 requests)')
# p.x_range = Range1d(0, 25000)
show(p)

In [52]:
p = BoxPlot(a1, values='Turn_Around_Time_ms', label=['use_case'], 
            title='Architecture 1 (group by Use Case)',
            outliers=False,
            legend=False)
show(p)

In [83]:
tooltips=[('Key', '@Key'), ('Bytes Sent', '@Bytes_Sent'), ('Use Case', '@use_case')]
p = Scatter(a1, x='Bytes_Sent', y='Total_Time_ms',
            title='Architecture 1 (All Use Cases)',
            xlabel='Bytes Sent [bytes]', ylabel='Total S3 response time [ms]',
            tooltips=tooltips)
p.add_tools(ResizeTool())
show(p)

In [84]:
tooltips=[('Key', '@Key'), ('Bytes Sent', '@Bytes_Sent'), ('Use Case', '@use_case')]
p = Scatter(a1, x='Bytes_Sent', y='Turn_Around_Time_ms',
            xlabel='Bytes Sent [bytes]', ylabel='Turn-around S3 response time [ms]',
            tooltips=tooltips)
p.add_tools(ResizeTool())
show(p)

tooltips=[('Key', '@Key'), ('Bytes Sent', '@Bytes_Sent'), ('Use Case', '@use_case')]
p = figure(toolbar_location='above', title='Architecture 1 (All Use Cases)')
p.xaxis.axis_label = 'S3 actual response time [ms]'
p.yaxis.axis_label = 'Turnaround S3 time [ms]'
p.xaxis.axis_label = 'S3 actual response time [ms]'
p.yaxis.axis_label = 'Turnaround S3 time [ms]'
new_df = a1[['Turn_Around_Time_ms', 'Key', 'Bytes_Sent', 'use_case']].copy()
new_df['actual'] = a1['Total_Time_ms'] - a1['Turn_Around_Time_ms']
p.scatter(x='actual', y='Turn_Around_Time_ms', source=ColumnDataSource(new_df), 
          color='red', size=4,
          name = 'scatter')
hover = HoverTool(names=['scatter'], tooltips=tooltips)
p.add_tools(ResizeTool(), hover)
show(p)

In [53]:
p = Histogram(a1['Turn_Around_Time_ms']/a1['Total_Time_ms'], bins=50, title='Architecture 1 (All Use Cases)',
              xlabel='Ratio of S3 turnaround vs total time', ylabel='Count(S3 requests)')
# p.x_range = Range1d(0, 25000)
show(p)

In [54]:
show(Histogram(a1['Trans_Rate_MB/s'], bins=50,
               xlabel='Transfer Rate [MB/s]', ylabel='Count(S3 requests)'))

## Architecture 2

S3 requests for Architecture 2:

In [55]:
a2 = s3l[s3l.arch == 'A2CFT']
len(a2.index)

659432

For Architecture \#2, the number of bytes sent and object size should **not** be the same for all S3 requests:

In [56]:
(a2.Bytes_Sent == a2.Object_Size).all()

False

Percentage reduction in the number of bytes pulled out of S3 compared to the original object sizes:

In [57]:
s3_bytes_savings(a2)

-99.94856049224019

This architecture uses HTTP range `GET`s. What are HTTP response codes? (Hint: They should all be [206](https://httpstatuses.com/206]).)

In [58]:
a2.HTTP_status.unique()

array([206])

In [82]:
p = Histogram(a2['Total_Time_ms'], bins=75, title='Architecture 2 (All Use Cases)',
              xlabel='Total S3 response time [ms]', ylabel='Count(S3 requests)')
#p.x_range = Range1d(0, 1500)
show(p)

In [60]:
p = BoxPlot(a2, values='Total_Time_ms', label=['use_case'], 
            title='Architecture 2 (group by Use Case)',
            outliers=False,
            legend=False)
show(p)

In [61]:
p = Histogram(a2['Turn_Around_Time_ms'], bins=50, title='Architecture 2 (All Use Cases)',
              xlabel='Turn-around S3 time [ms]', ylabel='Count(S3 requests)')
# p.x_range = Range1d(0, 25000)
show(p)

In [62]:
p = BoxPlot(a2, values='Turn_Around_Time_ms', label=['use_case'], 
            title='Architecture 2 (group by Use Case)',
            outliers=False,
            legend=False)
show(p)

tooltips=[('Key', '@Key'), ('Bytes Sent', '@Bytes_Sent'), ('Use Case', '@use_case')]
p = Scatter(a2, x='Bytes_Sent', y='Total_Time_ms', title='Architecture 2 (All Use Cases)',
            xlabel='Bytes Sent [bytes]', ylabel='Total S3 response time [ms]',
            tooltips=tooltips)
p.add_tools(ResizeTool())
show(p)

tooltips=[('Key', '@Key'), ('Bytes_Sent', '@Bytes_Sent'), ('Use Case', '@use_case')]
p = Scatter(a2, x='Bytes_Sent', y='Turn_Around_Time_ms',
            xlabel='Bytes Sent [bytes]', ylabel='Turn-around S3 response time [ms]',
            tooltips=tooltips)
p.add_tools(ResizeTool())
show(p)

tooltips=[('Key', '@Key'), ('Bytes Sent', '@Bytes_Sent'), ('Use Case', '@use_case')]
p = figure(toolbar_location='above', title='Architecture 2 (All Use Cases)')
p.xaxis.axis_label = 'S3 actual response time [ms]'
p.yaxis.axis_label = 'Turnaround S3 time [ms]'
p.xaxis.axis_label = 'S3 actual response time [ms]'
p.yaxis.axis_label = 'Turnaround S3 time [ms]'
new_df = a2[['Turn_Around_Time_ms', 'Key', 'Bytes_Sent', 'use_case']].copy()
new_df['actual'] = a2['Total_Time_ms'] - a2['Turn_Around_Time_ms']
p.scatter(x='actual', y='Turn_Around_Time_ms', source=ColumnDataSource(new_df), 
          color='red', size=8,
          name = 'scatter')
hover = HoverTool(names=['scatter'], tooltips=tooltips)
p.add_tools(ResizeTool(), hover)
show(p)

In [63]:
p = Histogram(a2['Turn_Around_Time_ms']/a2['Total_Time_ms'], bins=50, 
              title='Architecture 2 (All Use Cases)',
              xlabel='Ratio of S3 turnaround vs total time', ylabel='Count(S3 requests)')
# p.x_range = Range1d(0, 25000)
show(p)

In [64]:
p = Histogram(a2['Trans_Rate_MB/s'], bins=50,
              xlabel='Transfer Rate [MB/s]', ylabel='Count(S3 requests)')
#p.x_range = Range1d(0, 120)
show(p)

## Architecture 3

S3 requests for Architecture 3:

In [65]:
a3 = s3l[s3l.arch == 'A3CFT']
len(a3.index)

640549

For Architecture \#3, the number of bytes sent and object size should **be** the same for all S3 requests:

In [66]:
(a3.Bytes_Sent == a3.Object_Size).all()

False

Percentage reduction in the number of bytes pulled out of S3 compared to the original object sizes:

In [67]:
s3_bytes_savings(a3)

-63.894244026430314

In [81]:
p = Histogram(a3['Total_Time_ms'], bins=75, title='Architecture 3 (All Use Cases)',
              xlabel='Total S3 response time [ms]', ylabel='Count(S3 requests)')
#p.x_range = Range1d(0, 1500)
show(p)

In [69]:
p = BoxPlot(a3, values='Total_Time_ms', label=['use_case'], 
            title='Architecture 3 (group by Use Case)',
            outliers=False,
            legend=False)
show(p)

In [70]:
p = Histogram(a3['Turn_Around_Time_ms'], bins=50, title='Architecture 3 (All Use Cases)',
              xlabel='Turn-around S3 time [ms]', ylabel='Count(S3 requests)')
# p.x_range = Range1d(0, 25000)
show(p)

In [71]:
p = BoxPlot(a3, values='Turn_Around_Time_ms', label=['use_case'], 
            title='Architecture 3 (group by Use Case)',
            outliers=False,
            legend=False)
show(p)

tooltips=[('Key', '@Key'), ('Bytes Sent', '@Bytes_Sent'), ('Use Case', '@use_case')]
p = Scatter(a3, x='Bytes_Sent', y='Total_Time_ms', title='Architecture 3 (All Use Cases)',
            xlabel='Bytes Sent [bytes]', ylabel='Total S3 response time [ms]',
            tooltips=tooltips)
p.add_tools(ResizeTool())
show(p)

tooltips=[('Key', '@Key'), ('Bytes Sent', '@Bytes_Sent'), ('Use Case', '@use_case')]
p = Scatter(a3, x='Bytes_Sent', y='Turn_Around_Time_ms',
            xlabel='Bytes Sent [bytes]', ylabel='Turn-around S3 response time [ms]',
            tooltips=tooltips)
p.add_tools(ResizeTool())
show(p)

tooltips=[('Key', '@Key'), ('Bytes Sent', '@Bytes_Sent'), ('Use Case', '@use_case')]
p = figure(toolbar_location='above', title='Architecture 3 (All Use Cases)')
p.xaxis.axis_label = 'S3 actual response time [ms]'
p.yaxis.axis_label = 'Turnaround S3 time [ms]'
new_df = a3[['Turn_Around_Time_ms', 'Key', 'Bytes_Sent', 'use_case']].copy()
new_df['actual'] = a3['Total_Time_ms'] - a3['Turn_Around_Time_ms']
p.scatter(x='actual', y='Turn_Around_Time_ms', source=ColumnDataSource(new_df),
          color='red', size=8,
         name = 'scatter')
hover = HoverTool(names=['scatter'], tooltips=tooltips)
p.add_tools(ResizeTool(), hover)
show(p)

In [72]:
p = Histogram(a3['Turn_Around_Time_ms']/a3['Total_Time_ms'], bins=50, 
              title='Architecture 3 (All Use Cases)',
              xlabel='Ratio of S3 turnaround vs total time', ylabel='Count(S3 requests)')
# p.x_range = Range1d(0, 25000)
show(p)

In [73]:
p = Histogram(a3['Trans_Rate_MB/s'], bins=50,
              xlabel='Transfer Rate [MB/s]', ylabel='Count(S3 requests)')
#p.x_range = Range1d(0, 120)
show(p)

## Use Cases on Different Architectures

In [74]:
grp = s3l.groupby(['use_case', 'arch'])

### S3 Total Response Time

In [75]:
grp['Total_Time_ms'].describe().unstack()

count         mean          std     min      25%     50%  \
use_case arch                                                                 
UC10     A1CFT     365.0  5090.961644  1834.533756  4158.0  4452.00  4555.0   
         A2CFT     730.0   114.243836   122.972749    11.0    67.00    89.0   
         A3CFT     730.0   101.502740   120.415949    31.0    56.00    70.0   
UC11     A1CFT     364.0  5218.167582  2080.158387  4140.0  4451.00  4544.5   
         A2CFT    2920.0    73.280137   110.174552     7.0    25.00    49.0   
         A3CFT    2920.0    93.887671   125.312377    26.0    54.00    67.0   
UC12     A1CFT     439.0  1819.908884   856.011112  1506.0  1564.00  1613.0   
         A2CFT    1717.0    86.397787   140.466135     7.0    33.00    62.0   
         A3CFT    1717.0    61.285964    95.556378    11.0    30.00    39.0   
UC13     A1CFT     438.0  1778.769406   659.674331  1509.0  1560.00  1614.5   
         A2CFT    6829.0    42.599356    91.471768     6.0    10.00    19.0   
         A3CFT    6829.0    63.144091   271.753433    10.0    29.00    37.0   
UC14     A1CFT    4387.0  1787.716207   694.757734  1455.0  1560.00  1611.0   
         A2CFT    9499.0    67.927992   112.125672     6.0    21.00    41.0   
         A3CFT    9071.0    66.344063   117.666503     6.0    31.00    40.0   
UC15     A1CFT    3649.0  5151.830364  2489.331111  4115.0  4449.00  4529.0   
         A2CFT   10218.0    70.590135   127.753872     7.0    23.00    44.0   
         A3CFT    9486.0    90.141155   118.864678    17.0    50.00    62.0   
UC16     A2CFT     722.0   118.146814   137.120660     9.0    65.00    86.0   
         A3CFT     748.0    65.606952    83.520099    12.0    34.00    42.0   
UC17     A2CFT    1066.0   109.565666   149.008088     9.0    59.00    78.0   
         A3CFT    1078.0    94.913729   113.276045    26.0    54.00    67.0   
UC18     A2CFT   96839.0    35.425614   110.572926     5.0    10.00    12.0   
         A3CFT   96590.0    62.538979   161.989137     3.0    29.00    37.0   
UC19     A2CFT   86753.0    44.333764   125.331366     5.0    12.00    21.0   
         A3CFT   86729.0    89.228021   246.338820     5.0    46.00    64.0   
UC2      A2CFT       4.0    62.000000    66.987561    21.0    26.25    32.5   
         A3CFT      71.0    51.042254   127.662327     8.0    10.00    21.0   
UC20     A2CFT  292221.0    38.147060   173.516412     5.0    10.00    13.0   
         A3CFT  281081.0    63.117632   193.819407     3.0    28.00    37.0   
UC21     A2CFT  148682.0    43.602554   126.610514     6.0    12.00    19.0   
         A3CFT  142269.0    85.529321   143.497304     3.0    41.00    61.0   
UC6      A1CFT     439.0  1916.150342  1364.178573  1497.0  1564.00  1617.0   
         A2CFT     865.0   106.443931   114.812002     9.0    63.00    82.0   
         A3CFT     865.0    69.101734    97.533393     8.0    33.00    42.0   
UC7      A1CFT     365.0  5414.819178  2549.014046  4232.0  4453.00  4578.0   
         A2CFT     367.0   127.166213   134.871836    46.0    83.00    98.0   
         A3CFT     365.0   111.134247   144.256758    34.0    58.00    74.0   

                    75%      max  
use_case arch                     
UC10     A1CFT  4777.00  20202.0  
         A2CFT   117.00   1595.0  
         A3CFT    96.00   1174.0  
UC11     A1CFT  4784.00  18095.0  
         A2CFT    81.00   1317.0  
         A3CFT    94.00   2576.0  
UC12     A1CFT  1757.50  10672.0  
         A2CFT    97.00   3323.0  
         A3CFT    55.00   1689.0  
UC13     A1CFT  1743.00  10509.0  
         A2CFT    42.00   1867.0  
         A3CFT    51.00  19275.0  
UC14     A1CFT  1732.00  10391.0  
         A2CFT    77.00   2184.0  
         A3CFT    56.00   3334.0  
UC15     A1CFT  4708.00  68037.0  
         A2CFT    69.00   2764.0  
         A3CFT    86.00   3618.0  
UC16     A2CFT   117.75   1298.0  
         A3CFT    57.25    792.0  
UC17     A2CFT   110.00   2724.0  
         A3CFT    92.00   1782.0  
UC18     A2CFT    

In [76]:
uc_boxplots(s3l, 'Total_Time_ms', width=325, height=325)

### S3 Turnaround Time

In [77]:
grp['Turn_Around_Time_ms'].describe().unstack()

count        mean         std   min    25%    50%     75%  \
use_case arch                                                                  
UC10     A1CFT     365.0  117.090411   59.283775  54.0  84.00  100.0  127.00   
         A2CFT     730.0   90.502740   59.947010   8.0  60.00   81.0  103.00   
         A3CFT     730.0   84.427397   80.358598  29.0  53.00   66.0   87.00   
UC11     A1CFT     364.0  120.494505  100.158896  55.0  83.00   97.5  126.50   
         A2CFT    2920.0   56.294178   64.610638   5.0  21.75   44.0   71.00   
         A3CFT    2920.0   82.542466  107.762161  24.0  51.00   63.0   85.25   
UC12     A1CFT     439.0  119.717540   80.837271  53.0  83.00   99.0  126.00   
         A2CFT    1717.0   73.571928  101.958114   6.0  29.00   59.0   92.00   
         A3CFT    1717.0   50.535236   48.402854  10.0  29.00   38.0   52.00   
UC13     A1CFT     438.0  118.321918   70.825883  42.0  81.25   98.0  129.00   
         A2CFT    6829.0   33.922829   53.452132   5.0   9.00   18.0   37.00   
         A3CFT    6829.0   50.020794   84.030608   9.0  28.00   36.0   49.00   
UC14     A1CFT    4387.0  120.505357   89.922342  45.0  84.00  101.0  128.00   
         A2CFT    9499.0   54.810822   61.726345   5.0  19.00   38.0   72.00   
         A3CFT    9071.0   53.464116   64.095575   5.0  30.00   38.0   52.00   
UC15     A1CFT    3649.0  114.825158  116.746941  46.0  82.00   97.0  121.00   
         A2CFT   10218.0   50.229986   62.535295   5.0  20.00   37.0   59.00   
         A3CFT    9486.0   74.471537   74.205574  13.0  47.00   59.0   78.00   
UC16     A2CFT     722.0   97.307479   71.618768   8.0  63.00   84.0  111.00   
         A3CFT     748.0   57.481283   65.654187  12.0  33.00   40.5   53.00   
UC17     A2CFT    1066.0   87.174484  104.195399   7.0  54.00   72.0   98.00   
         A3CFT    1078.0   79.056586   59.747546  25.0  51.00   63.0   84.00   
UC18     A2CFT   96839.0   24.236330   56.454852   5.0   9.00   11.0   22.00   
         A3CFT   96590.0   49.592235   79.379345   3.0  28.00   36.0   48.00   
UC19     A2CFT   86753.0   29.427397   57.747785   5.0   9.00   18.0   31.00   
         A3CFT   86729.0   71.456918   72.552615   4.0  43.00   60.0   82.00   
UC2      A2CFT       4.0   61.000000   66.987561  20.0  25.25   31.5   67.25   
         A3CFT      71.0   33.746479   37.259598   7.0   9.00   20.0   40.50   
UC20     A2CFT  292221.0   24.589841   64.839532   5.0   9.00   11.0   22.00   
         A3CFT  281081.0   49.058759   71.936651   3.0  27.00   35.0   48.00   
UC21     A2CFT  148682.0   27.971442   73.627269   5.0   9.00   16.0   24.00   
         A3CFT  142269.0   69.044570   78.300279   2.0  38.00   57.0   80.00   
UC6      A1CFT     439.0  118.542141   68.507023  51.0  85.00   99.0  126.00   
         A2CFT     865.0   95.448555   94.672902   8.0  61.00   79.0  103.00   
         A3CFT     865.0   57.292486   56.978381   7.0  32.00   41.0   56.00   
UC7      A1CFT     365.0  115.295890   51.766170  54.0  83.00  100.0  130.00   
         A2CFT     367.0  108.000000   57.047291  43.0  79.00   93.0  116.00   
         A3CFT     365.0   89.695890   82.369765  31.0  55.00   70.0   97.00   

                    max  
use_case arch            
UC10     A1CFT    506.0  
         A2CFT    779.0  
         A3CFT   1173.0  
UC11     A1CFT   1352.0  
         A2CFT   1150.0  
         A3CFT   2574.0  
UC12     A1CFT   1191.0  
         A2CFT   3240.0  
         A3CFT    808.0  
UC13     A1CFT    864.0  
         A2CFT   1329.0  
         A3CFT   4346.0  
UC14     A1CFT   2020.0  
         A2CFT   1345.0  
         A3CFT   3334.0  
UC15     A1CFT   6100.0  
         A2CFT   1882.0  
         A3CFT   3617.0  
UC16     A2CFT    904.0  
         A3CFT    756.0  
UC17     A2CFT   2721.0  
         A3CFT    869.0  
UC18     A2CFT   4446.0  
         A3CFT  11152.0  
UC19     A2CFT   4376.0  
         A3CFT   4265.0  
UC2      A2CFT    161.0  
         A3CFT    173.0  
UC20     A2CFT  12754.0  
         A3C

In [78]:
uc_boxplots(s3l, 'Turn_Around_Time_ms', width=325, height=325)

### Bytes Sent in S3 Responses

In [79]:
grp['Bytes_Sent'].describe().unstack()

count          mean           std          min  \
use_case arch                                                       
UC10     A1CFT     365.0  3.174992e+08  4.251460e+06  297674188.0   
         A2CFT     730.0  1.820207e+05  1.187592e+04     146492.0   
         A3CFT     730.0  1.820207e+05  1.187592e+04     146492.0   
UC11     A1CFT     364.0  3.174964e+08  4.256981e+06  297674188.0   
         A2CFT    2920.0  1.848466e+05  9.133132e+03     146492.0   
         A3CFT    2920.0  1.848466e+05  9.133132e+03     146492.0   
UC12     A1CFT     439.0  1.143688e+08  8.441981e+06  112519317.0   
         A2CFT    1717.0  4.566393e+04  6.869919e+04      32735.0   
         A3CFT    1717.0  4.566393e+04  6.869919e+04      32735.0   
UC13     A1CFT     438.0  1.143721e+08  8.451355e+06  112519317.0   
         A2CFT    6829.0  3.147831e+04  3.671263e+04       3750.0   
         A3CFT    6829.0  3.147831e+04  3.671263e+04       3750.0   
UC14     A1CFT    4387.0  1.143698e+08  8.436126e+06  112519317.0   
         A2CFT    9499.0  4.439870e+04  9.338237e+04      10167.0   
         A3CFT    9071.0  4.298729e+04  9.569339e+04       3750.0   
UC15     A1CFT    3649.0  3.174989e+08  4.246763e+06  297674188.0   
         A2CFT   10218.0  1.841318e+05  8.564476e+03     146492.0   
         A3CFT    9486.0  1.859766e+05  9.891017e+03     146492.0   
UC16     A2CFT     722.0  4.584271e+04  1.070422e+05       4197.0   
         A3CFT     748.0  4.570368e+04  1.051565e+05       4197.0   
UC17     A2CFT    1066.0  1.853150e+05  9.173066e+03     147701.0   
         A3CFT    1078.0  1.849662e+05  8.833239e+03     152948.0   
UC18     A2CFT   96839.0  3.917933e+04  3.517547e+04          4.0   
         A3CFT   96590.0  3.766178e+04  7.453839e+03         12.0   
UC19     A2CFT   86753.0  1.939793e+05  8.477120e+04       3421.0   
         A3CFT   86729.0  1.940063e+05  8.481082e+04       3421.0   
UC2      A2CFT       4.0  4.879450e+04  5.603590e+04        217.0   
         A3CFT      71.0  3.913183e+04  1.455867e+04         12.0   
UC20     A2CFT  292221.0  3.593687e+04  1.067758e+04          4.0   
         A3CFT  281081.0  3.592469e+04  1.070879e+04         12.0   
UC21     A2CFT  148682.0  2.003219e+05  2.073061e+05         20.0   
         A3CFT  142269.0  1.995940e+05  2.067468e+05          8.0   
UC6      A1CFT     439.0  1.143688e+08  8.441981e+06  112519317.0   
         A2CFT     865.0  5.155292e+04  9.644113e+04      35044.0   
         A3CFT     865.0  5.155292e+04  9.644113e+04      35044.0   
UC7      A1CFT     365.0  3.174992e+08  4.251460e+06  297674188.0   
         A2CFT     367.0  1.912568e+05  6.262830e+03     154750.0   
         A3CFT     365.0  1.912665e+05  6.278618e+03     154750.0   

                         25%          50%           75%          max  
use_case arch                                                         
UC10     A1CFT  3.166932e+08  318602372.0  3.197686e+08  323612711.0  
         A2CFT  1.702430e+05     182015.0  1.937882e+05     202815.0  
         A3CFT  1.702430e+05     182015.0  1.937882e+05     202815.0  
UC11     A1CFT  3.166911e+08  318606885.0  3.197704e+08  323612711.0  
         A2CFT  1.793038e+05     186876.0  1.922675e+05     202815.0  
         A3CFT  1.793038e+05     186876.0  1.922675e+05     202815.0  
UC12     A1CFT  1.128264e+08  112904688.0  1.129860e+08  162646153.0  
         A2CFT  3.884700e+04      40059.0  4.087000e+04     831744.0  
         A3CFT  3.884700e+04      40059.0  4.087000e+04     831744.0  
UC13     A1CFT  1.128261e+08  112904189.5  1.129860e+08  162646153.0  
         A2CFT  1.895200e+04      35108.0  4.078800e+04     831744.0  
         A3CFT  1.895200e+04      35108.0  4.078800e+04     831744.0  
UC14     A1CFT  1.128258e+08  112904688.0  1.129861e+08  162646153.0  
         A2CFT  2.054700e+04      40183.0  4.157050e+04     831744.0  
         A3CFT  2.046750e+04      37778.0  4.059750e+04     831744.0  
UC15     A1CFT  3.166932e+08  318602372.0  3.197686

In [80]:
uc_boxplots(s3l, 'Bytes_Sent', width=325, height=325)

---

---

**OLD STUFF BELOW**

---

---

## Splitting Log Entries

The log entries will be split based on the product: AIRS and MERRA2.

## Analysis of AIRS Files Log Entries

## Analysis of MERRA2 Files Log Entries